In [1]:
import pandas as pd
import scipy.stats as stats

from sklearn import metrics, model_selection
from catboost import CatBoostClassifier

In [2]:
df_train = pd.read_csv('../../Feature_Encoding/data/train_helmert_encoding.csv')
df_test = pd.read_csv('../../Feature_Encoding/data/test_helmert_encoding.csv')
train = pd.read_csv('../../Feature_Engineering/data/other-cleaned_train.csv')

In [3]:
def cross_val(model, x_train, y_train):
    score_cross_val = model_selection.cross_val_score(model, x_train, y_train, cv=5)
    print(score_cross_val.mean())

In [4]:
#Realiza busqueda completa combinando los parametros
def catboost(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb = {'n_estimators': [50, 100, 200], 'learning_rate': [0.01, 0.05, 0.1], 'l2_leaf_reg': [0, 1, 5]}    
    catb_gs = model_selection.GridSearchCV(catb_classifier, params_catb, cv=5)
    catb_gs.fit(x_train, y_train)
    catb_best = catb_gs.best_estimator_
    print(catb_gs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [5]:
#Realiza busqueda random dentro de los parametros validos
def catboost2(x_train, y_train, x_validation, y_validation):
    catb_classifier = CatBoostClassifier()
    params_catb_2={
        'n_estimators':stats.randint(10,500),'learning_rate':stats.uniform(0.01,0.3),
        'subsample':stats.uniform(0.3,0.7),'l2_leaf_reg':[1,5,10],
        'max_depth':[3,10,6],'colsample_bylevel':stats.uniform(0.,0.6)
    }
    
    catb_rs = model_selection.RandomizedSearchCV(CatBoostClassifier(),
                          param_distributions=params_catb_2,
                          cv=2,
                          scoring='neg_log_loss',
                          verbose=1,
                          n_iter=200)
    
    catb_rs.fit(x_train, y_train)
    catb_best = catb_rs.best_estimator_
    print(catb_rs.best_params_)
    print('catb: {}'.format(catb_best.score(x_validation, y_validation)))
    return catb_best

In [6]:
def test_model(model, x_test, y_test):
    predictions = model.predict_proba(x_test)[:,1]
    logloss = metrics.log_loss(y_test, predictions)
    accuracy = metrics.accuracy_score(y_test, predictions.round())
    print("Accuracy: %.2f%%, Logloss: %.2f" % (accuracy*100.0, logloss))

In [7]:
y = train.Target
x_train, x_validation, y_train, y_validation = model_selection.train_test_split(df_train, y, test_size=0.3, stratify=y)

In [8]:
catboost_c = catboost(x_train, y_train, x_validation, y_validation)
test_model(catboost_c, x_validation, y_validation)
cross_val(catboost_c, x_train, y_train)

0:	learn: 0.6846197	total: 101ms	remaining: 4.95s
1:	learn: 0.6735346	total: 137ms	remaining: 3.28s
2:	learn: 0.6634098	total: 166ms	remaining: 2.61s
3:	learn: 0.6527216	total: 192ms	remaining: 2.21s
4:	learn: 0.6432699	total: 246ms	remaining: 2.22s
5:	learn: 0.6356349	total: 272ms	remaining: 1.99s
6:	learn: 0.6279845	total: 292ms	remaining: 1.79s
7:	learn: 0.6192733	total: 313ms	remaining: 1.65s
8:	learn: 0.6086900	total: 341ms	remaining: 1.55s
9:	learn: 0.6008272	total: 364ms	remaining: 1.46s
10:	learn: 0.5923800	total: 386ms	remaining: 1.37s
11:	learn: 0.5857763	total: 406ms	remaining: 1.28s
12:	learn: 0.5799657	total: 432ms	remaining: 1.23s
13:	learn: 0.5728658	total: 454ms	remaining: 1.17s
14:	learn: 0.5667240	total: 474ms	remaining: 1.11s
15:	learn: 0.5611553	total: 508ms	remaining: 1.08s
16:	learn: 0.5541177	total: 538ms	remaining: 1.04s
17:	learn: 0.5483283	total: 565ms	remaining: 1s
18:	learn: 0.5411432	total: 602ms	remaining: 982ms
19:	learn: 0.5344106	total: 625ms	remaining:

15:	learn: 0.5556987	total: 453ms	remaining: 963ms
16:	learn: 0.5499540	total: 471ms	remaining: 914ms
17:	learn: 0.5432437	total: 504ms	remaining: 896ms
18:	learn: 0.5359807	total: 532ms	remaining: 868ms
19:	learn: 0.5292938	total: 563ms	remaining: 844ms
20:	learn: 0.5231225	total: 604ms	remaining: 835ms
21:	learn: 0.5161518	total: 633ms	remaining: 805ms
22:	learn: 0.5121104	total: 651ms	remaining: 764ms
23:	learn: 0.5067589	total: 674ms	remaining: 730ms
24:	learn: 0.5013171	total: 693ms	remaining: 693ms
25:	learn: 0.4945183	total: 721ms	remaining: 666ms
26:	learn: 0.4904147	total: 756ms	remaining: 644ms
27:	learn: 0.4858923	total: 779ms	remaining: 612ms
28:	learn: 0.4818019	total: 803ms	remaining: 582ms
29:	learn: 0.4765530	total: 826ms	remaining: 551ms
30:	learn: 0.4713418	total: 848ms	remaining: 520ms
31:	learn: 0.4674954	total: 874ms	remaining: 491ms
32:	learn: 0.4632284	total: 896ms	remaining: 461ms
33:	learn: 0.4589763	total: 918ms	remaining: 432ms
34:	learn: 0.4542671	total: 942

80:	learn: 0.3440564	total: 3.29s	remaining: 772ms
81:	learn: 0.3429020	total: 3.34s	remaining: 733ms
82:	learn: 0.3411919	total: 3.38s	remaining: 692ms
83:	learn: 0.3398207	total: 3.42s	remaining: 651ms
84:	learn: 0.3385369	total: 3.46s	remaining: 611ms
85:	learn: 0.3367859	total: 3.52s	remaining: 573ms
86:	learn: 0.3355377	total: 3.57s	remaining: 533ms
87:	learn: 0.3341039	total: 3.61s	remaining: 493ms
88:	learn: 0.3325348	total: 3.67s	remaining: 454ms
89:	learn: 0.3313476	total: 3.73s	remaining: 414ms
90:	learn: 0.3300349	total: 3.78s	remaining: 374ms
91:	learn: 0.3290357	total: 3.82s	remaining: 332ms
92:	learn: 0.3277561	total: 3.87s	remaining: 291ms
93:	learn: 0.3267544	total: 3.91s	remaining: 249ms
94:	learn: 0.3255677	total: 3.95s	remaining: 208ms
95:	learn: 0.3241238	total: 3.98s	remaining: 166ms
96:	learn: 0.3229673	total: 4.02s	remaining: 124ms
97:	learn: 0.3220985	total: 4.06s	remaining: 82.8ms
98:	learn: 0.3213276	total: 4.09s	remaining: 41.4ms
99:	learn: 0.3203286	total: 4

48:	learn: 0.4065687	total: 1.47s	remaining: 1.53s
49:	learn: 0.4035414	total: 1.5s	remaining: 1.5s
50:	learn: 0.4006073	total: 1.51s	remaining: 1.46s
51:	learn: 0.3978677	total: 1.53s	remaining: 1.42s
52:	learn: 0.3953496	total: 1.56s	remaining: 1.38s
53:	learn: 0.3926562	total: 1.58s	remaining: 1.34s
54:	learn: 0.3893244	total: 1.59s	remaining: 1.3s
55:	learn: 0.3869534	total: 1.62s	remaining: 1.27s
56:	learn: 0.3849462	total: 1.65s	remaining: 1.24s
57:	learn: 0.3828082	total: 1.67s	remaining: 1.21s
58:	learn: 0.3810008	total: 1.7s	remaining: 1.18s
59:	learn: 0.3783187	total: 1.72s	remaining: 1.15s
60:	learn: 0.3761671	total: 1.75s	remaining: 1.12s
61:	learn: 0.3743374	total: 1.77s	remaining: 1.09s
62:	learn: 0.3716676	total: 1.79s	remaining: 1.05s
63:	learn: 0.3682462	total: 1.81s	remaining: 1.02s
64:	learn: 0.3665329	total: 1.83s	remaining: 987ms
65:	learn: 0.3649136	total: 1.85s	remaining: 954ms
66:	learn: 0.3627968	total: 1.87s	remaining: 921ms
67:	learn: 0.3610569	total: 1.89s	r

14:	learn: 0.5660624	total: 445ms	remaining: 2.52s
15:	learn: 0.5598628	total: 465ms	remaining: 2.44s
16:	learn: 0.5541464	total: 487ms	remaining: 2.38s
17:	learn: 0.5475910	total: 512ms	remaining: 2.33s
18:	learn: 0.5404838	total: 534ms	remaining: 2.28s
19:	learn: 0.5339164	total: 551ms	remaining: 2.21s
20:	learn: 0.5274832	total: 574ms	remaining: 2.16s
21:	learn: 0.5206409	total: 597ms	remaining: 2.12s
22:	learn: 0.5162860	total: 617ms	remaining: 2.06s
23:	learn: 0.5110316	total: 636ms	remaining: 2.02s
24:	learn: 0.5061842	total: 659ms	remaining: 1.98s
25:	learn: 0.4991132	total: 676ms	remaining: 1.93s
26:	learn: 0.4945464	total: 694ms	remaining: 1.88s
27:	learn: 0.4891434	total: 712ms	remaining: 1.83s
28:	learn: 0.4850367	total: 729ms	remaining: 1.78s
29:	learn: 0.4800319	total: 747ms	remaining: 1.74s
30:	learn: 0.4749264	total: 765ms	remaining: 1.7s
31:	learn: 0.4709953	total: 783ms	remaining: 1.66s
32:	learn: 0.4670253	total: 801ms	remaining: 1.63s
33:	learn: 0.4633434	total: 818m

...

72:	learn: 0.1719688	total: 1.93s	remaining: 3.36s
73:	learn: 0.1708777	total: 1.97s	remaining: 3.35s
74:	learn: 0.1699154	total: 2s	remaining: 3.33s
75:	learn: 0.1691116	total: 2.03s	remaining: 3.31s
76:	learn: 0.1682802	total: 2.05s	remaining: 3.28s
77:	learn: 0.1677503	total: 2.08s	remaining: 3.26s
78:	learn: 0.1660604	total: 2.12s	remaining: 3.25s
79:	learn: 0.1653940	total: 2.15s	remaining: 3.22s
80:	learn: 0.1645692	total: 2.18s	remaining: 3.2s
81:	learn: 0.1638028	total: 2.2s	remaining: 3.17s
82:	learn: 0.1624846	total: 2.23s	remaining: 3.15s
83:	learn: 0.1616409	total: 2.26s	remaining: 3.12s
84:	learn: 0.1604230	total: 2.29s	remaining: 3.1s
85:	learn: 0.1597795	total: 2.31s	remaining: 3.06s
86:	learn: 0.1588108	total: 2.33s	remaining: 3.02s
87:	learn: 0.1576541	total: 2.35s	remaining: 2.99s
88:	learn: 0.1570918	total: 2.37s	remaining: 2.95s
89:	learn: 0.1556672	total: 2.38s	remaining: 2.91s
90:	learn: 0.1544777	total: 2.4s	remaining: 2.88s
91:	learn: 0.1538858	total: 2.43s	rema

37:	learn: 0.2122718	total: 909ms	remaining: 3.88s
38:	learn: 0.2105705	total: 937ms	remaining: 3.87s
39:	learn: 0.2078561	total: 972ms	remaining: 3.89s
40:	learn: 0.2066236	total: 993ms	remaining: 3.85s
41:	learn: 0.2054466	total: 1.01s	remaining: 3.82s
42:	learn: 0.2039458	total: 1.04s	remaining: 3.8s
43:	learn: 0.2030167	total: 1.06s	remaining: 3.76s
44:	learn: 0.2010605	total: 1.08s	remaining: 3.74s
45:	learn: 0.1994634	total: 1.12s	remaining: 3.75s
46:	learn: 0.1982198	total: 1.15s	remaining: 3.75s
47:	learn: 0.1969211	total: 1.18s	remaining: 3.73s
48:	learn: 0.1951112	total: 1.2s	remaining: 3.69s
49:	learn: 0.1941212	total: 1.22s	remaining: 3.65s
50:	learn: 0.1926684	total: 1.24s	remaining: 3.61s
51:	learn: 0.1913031	total: 1.25s	remaining: 3.57s
52:	learn: 0.1901331	total: 1.27s	remaining: 3.53s
53:	learn: 0.1876605	total: 1.29s	remaining: 3.5s
54:	learn: 0.1862086	total: 1.31s	remaining: 3.46s
55:	learn: 0.1853023	total: 1.33s	remaining: 3.43s
56:	learn: 0.1843169	total: 1.35s	

0:	learn: 0.6157995	total: 19.7ms	remaining: 3.92s
1:	learn: 0.5296931	total: 38ms	remaining: 3.76s
2:	learn: 0.4686996	total: 63.4ms	remaining: 4.17s
3:	learn: 0.4352315	total: 93.1ms	remaining: 4.56s
4:	learn: 0.4031870	total: 135ms	remaining: 5.25s
5:	learn: 0.3780552	total: 204ms	remaining: 6.59s
6:	learn: 0.3614760	total: 252ms	remaining: 6.96s
7:	learn: 0.3450384	total: 303ms	remaining: 7.28s
8:	learn: 0.3308580	total: 360ms	remaining: 7.65s
9:	learn: 0.3182997	total: 402ms	remaining: 7.63s
10:	learn: 0.3092398	total: 462ms	remaining: 7.94s
11:	learn: 0.3015202	total: 505ms	remaining: 7.92s
12:	learn: 0.2922081	total: 526ms	remaining: 7.57s
13:	learn: 0.2860983	total: 552ms	remaining: 7.34s
14:	learn: 0.2802679	total: 573ms	remaining: 7.07s
15:	learn: 0.2759102	total: 597ms	remaining: 6.87s
16:	learn: 0.2687149	total: 621ms	remaining: 6.69s
17:	learn: 0.2655256	total: 647ms	remaining: 6.54s
18:	learn: 0.2625913	total: 689ms	remaining: 6.57s
19:	learn: 0.2586907	total: 721ms	remai

161:	learn: 0.0938967	total: 4.73s	remaining: 1.11s
162:	learn: 0.0935135	total: 4.79s	remaining: 1.09s
163:	learn: 0.0929070	total: 4.86s	remaining: 1.07s
164:	learn: 0.0924264	total: 4.92s	remaining: 1.04s
165:	learn: 0.0920583	total: 4.95s	remaining: 1.01s
166:	learn: 0.0913238	total: 4.97s	remaining: 982ms
167:	learn: 0.0909013	total: 5s	remaining: 952ms
168:	learn: 0.0903265	total: 5.02s	remaining: 921ms
169:	learn: 0.0900082	total: 5.05s	remaining: 892ms
170:	learn: 0.0894198	total: 5.07s	remaining: 861ms
171:	learn: 0.0889555	total: 5.1s	remaining: 831ms
172:	learn: 0.0884824	total: 5.15s	remaining: 804ms
173:	learn: 0.0877938	total: 5.18s	remaining: 775ms
174:	learn: 0.0874154	total: 5.22s	remaining: 746ms
175:	learn: 0.0868816	total: 5.25s	remaining: 716ms
176:	learn: 0.0862505	total: 5.29s	remaining: 687ms
177:	learn: 0.0857291	total: 5.32s	remaining: 658ms
178:	learn: 0.0853715	total: 5.35s	remaining: 627ms
179:	learn: 0.0850201	total: 5.38s	remaining: 597ms
180:	learn: 0.08

122:	learn: 0.1272396	total: 3.42s	remaining: 2.14s
123:	learn: 0.1260305	total: 3.45s	remaining: 2.11s
124:	learn: 0.1250428	total: 3.49s	remaining: 2.09s
125:	learn: 0.1243510	total: 3.52s	remaining: 2.07s
126:	learn: 0.1239357	total: 3.55s	remaining: 2.04s
127:	learn: 0.1229028	total: 3.58s	remaining: 2.02s
128:	learn: 0.1221498	total: 3.62s	remaining: 1.99s
129:	learn: 0.1214933	total: 3.65s	remaining: 1.97s
130:	learn: 0.1206228	total: 3.68s	remaining: 1.94s
131:	learn: 0.1195520	total: 3.71s	remaining: 1.91s
132:	learn: 0.1185946	total: 3.74s	remaining: 1.89s
133:	learn: 0.1180281	total: 3.77s	remaining: 1.85s
134:	learn: 0.1170970	total: 3.79s	remaining: 1.82s
135:	learn: 0.1156467	total: 3.81s	remaining: 1.79s
136:	learn: 0.1148715	total: 3.84s	remaining: 1.76s
137:	learn: 0.1142928	total: 3.88s	remaining: 1.74s
138:	learn: 0.1135304	total: 3.9s	remaining: 1.71s
139:	learn: 0.1128713	total: 3.93s	remaining: 1.68s
140:	learn: 0.1120997	total: 3.95s	remaining: 1.65s
141:	learn: 0

In [9]:
catboost_2 = catboost2(x_train, y_train, x_validation, y_validation)
test_model(catboost_2, x_validation, y_validation)
cross_val(catboost_2, x_train, y_train)

Fitting 2 folds for each of 200 candidates, totalling 400 fits
0:	learn: 0.5609766	total: 11.1ms	remaining: 3.87s
1:	learn: 0.4952403	total: 19.7ms	remaining: 3.43s
2:	learn: 0.4510061	total: 32.7ms	remaining: 3.79s
3:	learn: 0.4176966	total: 44.2ms	remaining: 3.84s
4:	learn: 0.3905004	total: 52.1ms	remaining: 3.6s
5:	learn: 0.3730308	total: 64.9ms	remaining: 3.73s
6:	learn: 0.3634143	total: 79.7ms	remaining: 3.92s
7:	learn: 0.3610713	total: 83ms	remaining: 3.56s
8:	learn: 0.3475577	total: 90.1ms	remaining: 3.42s
9:	learn: 0.3410940	total: 101ms	remaining: 3.46s
10:	learn: 0.3350272	total: 115ms	remaining: 3.56s
11:	learn: 0.3302055	total: 123ms	remaining: 3.48s
12:	learn: 0.3255800	total: 135ms	remaining: 3.52s
13:	learn: 0.3185361	total: 141ms	remaining: 3.4s
14:	learn: 0.3159771	total: 152ms	remaining: 3.39s
15:	learn: 0.3118065	total: 158ms	remaining: 3.31s
16:	learn: 0.3093261	total: 166ms	remaining: 3.27s
17:	learn: 0.3018155	total: 176ms	remaining: 3.26s
18:	learn: 0.2999268	tot

167:	learn: 0.1546253	total: 1.29s	remaining: 1.4s
168:	learn: 0.1538245	total: 1.29s	remaining: 1.39s
169:	learn: 0.1532764	total: 1.3s	remaining: 1.38s
170:	learn: 0.1527940	total: 1.3s	remaining: 1.37s
171:	learn: 0.1524710	total: 1.32s	remaining: 1.37s
172:	learn: 0.1519155	total: 1.33s	remaining: 1.36s
173:	learn: 0.1515060	total: 1.33s	remaining: 1.36s
174:	learn: 0.1509745	total: 1.35s	remaining: 1.35s
175:	learn: 0.1505998	total: 1.35s	remaining: 1.34s
176:	learn: 0.1502044	total: 1.35s	remaining: 1.33s
177:	learn: 0.1497345	total: 1.36s	remaining: 1.32s
178:	learn: 0.1492610	total: 1.36s	remaining: 1.31s
179:	learn: 0.1489668	total: 1.37s	remaining: 1.3s
180:	learn: 0.1486350	total: 1.37s	remaining: 1.29s
181:	learn: 0.1482322	total: 1.38s	remaining: 1.28s
182:	learn: 0.1476683	total: 1.38s	remaining: 1.27s
183:	learn: 0.1468955	total: 1.39s	remaining: 1.26s
184:	learn: 0.1464108	total: 1.39s	remaining: 1.25s
185:	learn: 0.1460249	total: 1.4s	remaining: 1.24s
186:	learn: 0.145

330:	learn: 0.1024801	total: 2.24s	remaining: 135ms
331:	learn: 0.1023391	total: 2.24s	remaining: 128ms
332:	learn: 0.1020698	total: 2.24s	remaining: 121ms
333:	learn: 0.1017539	total: 2.25s	remaining: 115ms
334:	learn: 0.1015576	total: 2.26s	remaining: 108ms
335:	learn: 0.1014218	total: 2.26s	remaining: 101ms
336:	learn: 0.1010710	total: 2.27s	remaining: 94.2ms
337:	learn: 0.1008603	total: 2.27s	remaining: 87.4ms
338:	learn: 0.1006092	total: 2.28s	remaining: 80.8ms
339:	learn: 0.1004727	total: 2.29s	remaining: 74.1ms
340:	learn: 0.1001435	total: 2.31s	remaining: 67.6ms
341:	learn: 0.0999286	total: 2.31s	remaining: 60.8ms
342:	learn: 0.0997673	total: 2.32s	remaining: 54.1ms
343:	learn: 0.0996335	total: 2.33s	remaining: 47.3ms
344:	learn: 0.0993433	total: 2.34s	remaining: 40.6ms
345:	learn: 0.0990643	total: 2.35s	remaining: 33.9ms
346:	learn: 0.0989050	total: 2.36s	remaining: 27.2ms
347:	learn: 0.0987085	total: 2.37s	remaining: 20.4ms
348:	learn: 0.0984303	total: 2.38s	remaining: 13.6ms

148:	learn: 0.1581364	total: 1.36s	remaining: 1.84s
149:	learn: 0.1575721	total: 1.37s	remaining: 1.83s
150:	learn: 0.1572630	total: 1.38s	remaining: 1.82s
151:	learn: 0.1568008	total: 1.39s	remaining: 1.81s
152:	learn: 0.1565419	total: 1.39s	remaining: 1.8s
153:	learn: 0.1562506	total: 1.4s	remaining: 1.79s
154:	learn: 0.1558524	total: 1.41s	remaining: 1.79s
155:	learn: 0.1554366	total: 1.42s	remaining: 1.77s
156:	learn: 0.1549619	total: 1.43s	remaining: 1.77s
157:	learn: 0.1542778	total: 1.44s	remaining: 1.76s
158:	learn: 0.1533588	total: 1.45s	remaining: 1.75s
159:	learn: 0.1527192	total: 1.45s	remaining: 1.74s
160:	learn: 0.1523985	total: 1.46s	remaining: 1.73s
161:	learn: 0.1520794	total: 1.47s	remaining: 1.72s
162:	learn: 0.1516287	total: 1.48s	remaining: 1.71s
163:	learn: 0.1512976	total: 1.49s	remaining: 1.69s
164:	learn: 0.1510770	total: 1.5s	remaining: 1.69s
165:	learn: 0.1506031	total: 1.5s	remaining: 1.67s
166:	learn: 0.1502105	total: 1.51s	remaining: 1.66s
167:	learn: 0.15

317:	learn: 0.1039511	total: 2.48s	remaining: 257ms
318:	learn: 0.1037977	total: 2.48s	remaining: 249ms
319:	learn: 0.1035541	total: 2.49s	remaining: 241ms
320:	learn: 0.1034696	total: 2.5s	remaining: 233ms
321:	learn: 0.1031280	total: 2.5s	remaining: 225ms
322:	learn: 0.1028157	total: 2.51s	remaining: 217ms
323:	learn: 0.1024686	total: 2.52s	remaining: 210ms
324:	learn: 0.1023912	total: 2.52s	remaining: 202ms
325:	learn: 0.1022470	total: 2.52s	remaining: 194ms
326:	learn: 0.1021162	total: 2.53s	remaining: 186ms
327:	learn: 0.1016995	total: 2.53s	remaining: 178ms
328:	learn: 0.1014345	total: 2.54s	remaining: 170ms
329:	learn: 0.1011982	total: 2.55s	remaining: 162ms
330:	learn: 0.1010065	total: 2.55s	remaining: 154ms
331:	learn: 0.1007256	total: 2.56s	remaining: 146ms
332:	learn: 0.1005240	total: 2.56s	remaining: 139ms
333:	learn: 0.1003354	total: 2.56s	remaining: 131ms
334:	learn: 0.0999513	total: 2.57s	remaining: 123ms
335:	learn: 0.0997271	total: 2.57s	remaining: 115ms
336:	learn: 0.

...

106:	learn: 0.1002966	total: 9.67s	remaining: 15.4s
107:	learn: 0.0996323	total: 9.77s	remaining: 15.3s
108:	learn: 0.0991302	total: 9.85s	remaining: 15.2s
109:	learn: 0.0981482	total: 9.96s	remaining: 15.1s
110:	learn: 0.0968691	total: 10.1s	remaining: 15s
111:	learn: 0.0964740	total: 10.1s	remaining: 14.9s
112:	learn: 0.0955042	total: 10.2s	remaining: 14.8s
113:	learn: 0.0948732	total: 10.4s	remaining: 14.8s
114:	learn: 0.0943163	total: 10.5s	remaining: 14.8s
115:	learn: 0.0937015	total: 10.6s	remaining: 14.7s
116:	learn: 0.0929350	total: 10.7s	remaining: 14.6s
117:	learn: 0.0921186	total: 10.8s	remaining: 14.5s
118:	learn: 0.0913460	total: 10.8s	remaining: 14.4s
119:	learn: 0.0906088	total: 10.9s	remaining: 14.3s
120:	learn: 0.0897777	total: 11s	remaining: 14.2s
121:	learn: 0.0887314	total: 11.1s	remaining: 14.1s
122:	learn: 0.0883249	total: 11.2s	remaining: 14s
123:	learn: 0.0880228	total: 11.3s	remaining: 13.9s
124:	learn: 0.0876721	total: 11.4s	remaining: 13.8s
125:	learn: 0.0872

265:	learn: 0.0397328	total: 24.6s	remaining: 1.01s
266:	learn: 0.0395770	total: 24.7s	remaining: 923ms
267:	learn: 0.0394687	total: 24.8s	remaining: 832ms
268:	learn: 0.0393299	total: 24.9s	remaining: 740ms
269:	learn: 0.0391255	total: 25s	remaining: 648ms
270:	learn: 0.0389469	total: 25.1s	remaining: 556ms
271:	learn: 0.0388012	total: 25.3s	remaining: 464ms
272:	learn: 0.0385948	total: 25.4s	remaining: 372ms
273:	learn: 0.0384736	total: 25.5s	remaining: 279ms
274:	learn: 0.0380385	total: 25.6s	remaining: 186ms
275:	learn: 0.0379211	total: 25.7s	remaining: 93.1ms
276:	learn: 0.0377699	total: 25.8s	remaining: 0us
0:	learn: 0.5870370	total: 98.6ms	remaining: 27.2s
1:	learn: 0.5002686	total: 213ms	remaining: 29.2s
2:	learn: 0.4444604	total: 303ms	remaining: 27.6s
3:	learn: 0.4024408	total: 394ms	remaining: 26.9s
4:	learn: 0.3705557	total: 468ms	remaining: 25.5s
5:	learn: 0.3488740	total: 597ms	remaining: 27s
6:	learn: 0.3307949	total: 674ms	remaining: 26s
7:	learn: 0.3150768	total: 764ms

150:	learn: 0.0786084	total: 13.3s	remaining: 11.1s
151:	learn: 0.0783994	total: 13.4s	remaining: 11s
152:	learn: 0.0782772	total: 13.4s	remaining: 10.9s
153:	learn: 0.0778554	total: 13.5s	remaining: 10.8s
154:	learn: 0.0767638	total: 13.6s	remaining: 10.7s
155:	learn: 0.0763111	total: 13.7s	remaining: 10.6s
156:	learn: 0.0759257	total: 13.8s	remaining: 10.5s
157:	learn: 0.0753127	total: 13.9s	remaining: 10.5s
158:	learn: 0.0745844	total: 14s	remaining: 10.4s
159:	learn: 0.0743412	total: 14.1s	remaining: 10.3s
160:	learn: 0.0735053	total: 14.2s	remaining: 10.2s
161:	learn: 0.0732502	total: 14.3s	remaining: 10.1s
162:	learn: 0.0729677	total: 14.4s	remaining: 10.1s
163:	learn: 0.0725843	total: 14.5s	remaining: 9.96s
164:	learn: 0.0721071	total: 14.5s	remaining: 9.87s
165:	learn: 0.0715892	total: 14.7s	remaining: 9.8s
166:	learn: 0.0711513	total: 14.7s	remaining: 9.7s
167:	learn: 0.0707882	total: 14.8s	remaining: 9.6s
168:	learn: 0.0703908	total: 14.9s	remaining: 9.5s
169:	learn: 0.069952

35:	learn: 0.1923740	total: 3.41s	remaining: 22.8s
36:	learn: 0.1913415	total: 3.47s	remaining: 22.5s
37:	learn: 0.1896015	total: 3.55s	remaining: 22.3s
38:	learn: 0.1880908	total: 3.69s	remaining: 22.5s
39:	learn: 0.1864309	total: 3.76s	remaining: 22.3s
40:	learn: 0.1843421	total: 3.84s	remaining: 22.1s
41:	learn: 0.1825914	total: 3.94s	remaining: 22s
42:	learn: 0.1806733	total: 4.05s	remaining: 22s
43:	learn: 0.1776097	total: 4.2s	remaining: 22.2s
44:	learn: 0.1762970	total: 4.33s	remaining: 22.3s
45:	learn: 0.1741934	total: 4.47s	remaining: 22.5s
46:	learn: 0.1731256	total: 4.6s	remaining: 22.5s
47:	learn: 0.1718156	total: 4.74s	remaining: 22.6s
48:	learn: 0.1698294	total: 4.82s	remaining: 22.4s
49:	learn: 0.1693203	total: 4.89s	remaining: 22.2s
50:	learn: 0.1687055	total: 4.97s	remaining: 22s
51:	learn: 0.1671229	total: 5.06s	remaining: 21.9s
52:	learn: 0.1651059	total: 5.12s	remaining: 21.7s
53:	learn: 0.1642455	total: 5.22s	remaining: 21.5s
54:	learn: 0.1621029	total: 5.32s	remai

196:	learn: 0.0597119	total: 19s	remaining: 7.73s
197:	learn: 0.0589951	total: 19.2s	remaining: 7.65s
198:	learn: 0.0588145	total: 19.3s	remaining: 7.56s
199:	learn: 0.0584109	total: 19.4s	remaining: 7.47s
200:	learn: 0.0581209	total: 19.5s	remaining: 7.38s
201:	learn: 0.0579294	total: 19.6s	remaining: 7.28s
202:	learn: 0.0574487	total: 19.7s	remaining: 7.19s
203:	learn: 0.0569924	total: 19.8s	remaining: 7.1s
204:	learn: 0.0566155	total: 19.9s	remaining: 7s
205:	learn: 0.0565086	total: 20.1s	remaining: 6.92s
206:	learn: 0.0561795	total: 20.2s	remaining: 6.83s
207:	learn: 0.0556370	total: 20.3s	remaining: 6.73s
208:	learn: 0.0551957	total: 20.4s	remaining: 6.62s
209:	learn: 0.0548936	total: 20.4s	remaining: 6.52s
210:	learn: 0.0544533	total: 20.5s	remaining: 6.42s
211:	learn: 0.0541425	total: 20.6s	remaining: 6.32s
212:	learn: 0.0541405	total: 20.7s	remaining: 6.22s
213:	learn: 0.0539700	total: 20.8s	remaining: 6.12s
214:	learn: 0.0538218	total: 20.9s	remaining: 6.01s
215:	learn: 0.0537

In [10]:
y_pred = catboost_2.predict_proba(df_test)[:,1]
submission_catboost = pd.DataFrame(data={'Opportunity_ID':df_test['Opportunity_ID'], 'Target': y_pred})
submission_catboost = submission_catboost.groupby("Opportunity_ID").agg({"Target":"mean"}).reset_index()
submission_catboost.to_csv('../submits/helmert_catboost.csv', index=False)